<h1>Covid 19<h>

Active reporting on COVID-19 deaths will drastically improve civil and government measures. We will pull COVID-19 data and build an interactive nation wide map broken down by state and age group.

**Steps**

**1. Import Libraries**
**2. Process Data**
**3. Map Data**
**4. Feedback**

<h2> CDC Data <h>

https://data.cdc.gov/NCHS/Provisional-COVID-19-Death-Counts-by-Sex-Age-and-S/9bhg-hcku

In [1]:
import numpy as np 
import pandas as pd 
import requests 
import folium
!conda install -c conda-forge geopy --yes
!conda install -c conda-forge folium=0.5.0 --yes
from geopy.geocoders import Nominatim 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
!pip install lxml
!pip install beautifulsoup4
!pip install geocoder

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2020.4.5.2 |       hecda079_0         147 KB  conda-forge
    certifi-2020.4.5.2         |   py36h9f0ad1d_0         152 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-1.22.0               |     pyh9f0ad1d_0          63 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         395 KB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50-py_0
  geopy              conda-forge/noarch::geopy-1.22.0-pyh9f0ad1d_0

The following packages will be UPDATED:

  ca-certificates                     2020.4.5

Pull the Data, check it out.

In [145]:
df = pd.read_csv('https://data.cdc.gov/api/views/9bhg-hcku/rows.csv?accessType=DOWNLOAD')
df.dtypes

Data as of                                   object
Start week                                   object
End Week                                     object
State                                        object
Sex                                          object
Age group                                    object
COVID-19 Deaths                             float64
Total Deaths                                float64
Pneumonia Deaths                            float64
Pneumonia and COVID-19 Deaths               float64
Influenza Deaths                            float64
Pneumonia, Influenza, or COVID-19 Deaths    float64
Footnote                                     object
dtype: object

Trim Data

In [146]:
df1 = df.drop(columns=['Data as of', 'Start week', 'End Week', 'Sex', 'Total Deaths', 'Pneumonia Deaths', 
      'Pneumonia and COVID-19 Deaths', 'Influenza Deaths', 'Pneumonia, Influenza, or COVID-19 Deaths', 'Footnote'])
df1 = df1.rename(columns={"COVID-19 Deaths":"Deaths", "Age group":"Age"})
df1["Age"].replace({"Under 1 year": "0-1 years"}, inplace=True)
df1["State"].replace({"New York City" : "New York"}, inplace=True)
df1 = df1[(df1.State != 'United States') & (df1.Age != 'All ages') & (df1.Age != 'All Ages')]
df1 = df1.groupby(['State'], as_index = False).sum()
df1['State'] = df1['State'].replace({
    'Alabama': 'AL',
    'Alaska': 'AK',
    'American Samoa': 'AS',
    'Arizona': 'AZ',
    'Arkansas': 'AR',
    'California': 'CA',
    'Colorado': 'CO',
    'Connecticut': 'CT',
    'Delaware': 'DE',
    'District of Columbia': 'DC',
    'Florida': 'FL',
    'Georgia': 'GA',
    'Guam': 'GU',
    'Hawaii': 'HI',
    'Idaho': 'ID',
    'Illinois': 'IL',
    'Indiana': 'IN',
    'Iowa': 'IA',
    'Kansas': 'KS',
    'Kentucky': 'KY',
    'Louisiana': 'LA',
    'Maine': 'ME',
    'Maryland': 'MD',
    'Massachusetts': 'MA',
    'Michigan': 'MI',
    'Minnesota': 'MN',
    'Mississippi': 'MS',
    'Missouri': 'MO',
    'Montana': 'MT',
    'Nebraska': 'NE',
    'Nevada': 'NV',
    'New Hampshire': 'NH',
    'New Jersey': 'NJ',
    'New Mexico': 'NM',
    'New York': 'NY',
    'North Carolina': 'NC',
    'North Dakota': 'ND',
    'Northern Mariana Islands':'MP',
    'Ohio': 'OH',
    'Oklahoma': 'OK',
    'Oregon': 'OR',
    'Pennsylvania': 'PA',
    'Puerto Rico': 'PR',
    'Rhode Island': 'RI',
    'South Carolina': 'SC',
    'South Dakota': 'SD',
    'Tennessee': 'TN',
    'Texas': 'TX',
    'Utah': 'UT',
    'Vermont': 'VT',
    'Virgin Islands': 'VI',
    'Virginia': 'VA',
    'Washington': 'WA',
    'West Virginia': 'WV',
    'Wisconsin': 'WI',
    'Wyoming': 'WY'
})
df1

State   Deaths
0     AL    638.0
1     AK      0.0
2     AZ    799.0
3     AR     82.0
4     CA   3793.0
5     CO   1310.0
6     CT   2155.0
7     DE    346.0
8     DC    373.0
9     FL   2297.0
10    GA   1608.0
11    HI      0.0
12    ID     65.0
13    IL   4682.0
14    IN   1851.0
15    IA    464.0
16    KS    182.0
17    KY    366.0
18    LA   2191.0
19    ME     79.0
20    MD   2565.0
21    MA   6490.0
22    MI   4616.0
23    MN    982.0
24    MS    607.0
25    MO    661.0
26    MT      0.0
27    NE    141.0
28    NV    361.0
29    NH    239.0
30    NJ  11981.0
31    NM    262.0
32    NY  28289.0
33    NC    490.0
34    ND     10.0
35    OH   1597.0
36    OK    277.0
37    OR    157.0
38    PA   5732.0
39    PR      0.0
40    RI    536.0
41    SC    484.0
42    SD     15.0
43    TN    306.0
44    TX   1619.0
45    UT     87.0
46    VT     16.0
47    VA   1406.0
48    WA    925.0
49    WV     57.0
50    WI    536.0
51    WY      0.0

In [147]:
df2 = df.drop(columns=['Data as of', 'Start week', 'End Week', 'Sex', 'Total Deaths', 'Pneumonia Deaths', 
      'Pneumonia and COVID-19 Deaths', 'Influenza Deaths', 'Pneumonia, Influenza, or COVID-19 Deaths', 'Footnote'])
df2 = df2.rename(columns={"COVID-19 Deaths":"Deaths", "Age group":"Age"})
df2["Age"].replace({"Under 1 year": "0-1 years"}, inplace=True)
df2["State"].replace({"New York City" : "New York"}, inplace=True)
df2 = df2[(df2.State != 'United States') & (df2.Age != 'All ages') & (df2.Age != 'All Ages')]
df2 = df2.groupby(['State'], as_index = False).sum()
df3 = pd.read_html('https://developers.google.com/public-data/docs/canonical/states_csv')[0]
df3 = df3.rename(columns={"latitude": "Latitude", "longitude": "Longitude", "name":"State" })
df3 = df3.drop(columns='state')
df3 = df3[['State', 'Latitude', 'Longitude']]
df5 = pd.merge(df2, df3, on=('State'))
df5

State   Deaths   Latitude   Longitude
0                Alabama    638.0  32.318231  -86.902298
1                 Alaska      0.0  63.588753 -154.493062
2                Arizona    799.0  34.048928 -111.093731
3               Arkansas     82.0  35.201050  -91.831833
4             California   3793.0  36.778261 -119.417932
5               Colorado   1310.0  39.550051 -105.782067
6            Connecticut   2155.0  41.603221  -73.087749
7               Delaware    346.0  38.910832  -75.527670
8   District of Columbia    373.0  38.905985  -77.033418
9                Florida   2297.0  27.664827  -81.515754
10               Georgia   1608.0  32.157435  -82.907123
11                Hawaii      0.0  19.898682 -155.665857
12                 Idaho     65.0  44.068202 -114.742041
13              Illinois   4682.0  40.633125  -89.398528
14               Indiana   1851.0  40.551217  -85.602364
15                  Iowa    464.0  41.878003  -93.097702
16                Kansas    182.0  39.011902  -98.484246
17              Kentucky    366.0  37.839333  -84.270018
18             Louisiana   2191.0  31.244823  -92.145024
19                 Maine     79.0  45.253783  -69.445469
20              Maryland   2565.0  39.045755  -76.641271
21         Massachusetts   6490.0  42.407211  -71.382437
22              Michigan   4616.0  44.314844  -85.602364
23             Minnesota    982.0  46.729553  -94.685900
24           Mississippi    607.0  32.354668  -89.398528
25              Missouri    661.0  37.964253  -91.831833
26               Montana      0.0  46.879682 -110.362566
27              Nebraska    141.0  41.492537  -99.901813
28                Nevada    361.0  38.802610 -116.419389
29         New Hampshire    239.0  43.193852  -71.572395
30            New Jersey  11981.0  40.058324  -74.405661
31            New Mexico    262.0  34.972730 -105.032363
32              New York  28289.0  43.299428  -74.217933
33        North Carolina    490.0  35.759573  -79.019300
34          North Dakota     10.0  47.551493 -101.002012
35                  Ohio   1597.0  40.417287  -82.907123
36              Oklahoma    277.0  35.007752  -97.092877
37                Oregon    157.0  43.804133 -120.554201
38          Pennsylvania   5732.0  41.203322  -77.194525
39           Puerto Rico      0.0  18.220833  -66.590149
40          Rhode Island    536.0  41.580095  -71.477429
41        South Carolina    484.0  33.836081  -81.163725
42          South Dakota     15.0  43.969515  -99.901813
43             Tennessee    306.0  35.517491  -86.580447
44                 Texas   1619.0  31.968599  -99.901813
45                  Utah     87.0  39.320980 -111.093731
46               Vermont     16.0  44.558803  -72.577841
47              Virginia   1406.0  37.431573  -78.656894
48            Washington    925.0  47.751074 -120.740139
49         West Virginia     57.0  38.597626  -80.454903
50             Wisconsin    536.0  43.784440  -88.787868
51               Wyoming      0.0  43.075968 -107.290284

In [148]:
url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
state_geo = f'{url}/us-states.json'

In [149]:
Covid_19 = folium.Map(location=[37.0902, -95.7129], tiles='Stamen Toner', zoom_start=3,)
Covid_19.choropleth(geo_data=state_geo,
    data=df1,
    columns=['State', 'Deaths'],
    key_on='feature.id',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='CDC COVID 19 Deaths'
)

folium.LayerControl().add_to(Covid_19)

for lat, lng, State, Deaths in zip(df5['Latitude'], df5['Longitude'], df5['State'], df5['Deaths']):
    label = 'State: {} Deaths: {}'.format(State,Deaths)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_opacity=0.7,
        parse_html=False).add_to(Covid_19) 

Covid_19

**Feedback:CDC data is limited and suppressed, if you check the data itself "..suppressed in accordance with NCHS confidentiality standards." there is a clear indication that the data itself is very limited. The data was published May 7 as well during this notebook publishing.**